In [1]:
from bs4 import BeautifulSoup as bs
import pandas as pd
from pprint import pprint
import requests

Within this notebook I have scrapped files from IMDb for Orginal movies. This is an updated version of the previous list of Original movies. It contains over 3,000 new entries and was added to ensure that there was comparable information for both orginal(stand alone movies) and unoriginal movies.The list of original movies was taken from a data dump Nathan found on TMDb. This code was used to scrape information for unoriginal movies aswell. 

In [2]:
import pandas as pd

df = pd.read_csv('original_movies.csv')

# drop all columns except 'imdb_id'
df = df[['imdb_id']]

# save the newDataFrame to a CSV file
df.to_csv('original_movies.csv', index=False)

In [3]:
headers = {
    'Host': 'www.imdb.com',
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36'
}

In [4]:
def get_title_details(imdb_id):
    imdb_url = f'https://www.imdb.com/title/{imdb_id.strip()}/'

    page = bs(requests.get(imdb_url, headers=headers).text, 'lxml')
    
    return {
        'Budget': page.find('li', {'data-testid': 'title-boxoffice-budget'}).find('div').text if page.find('li', {'data-testid': 'title-boxoffice-budget'}) else '',
        'Box Office US/CA': page.find('li', {'data-testid': 'title-boxoffice-grossdomestic'}).find('div').text if page.find('li', {'data-testid': 'title-boxoffice-grossdomestic'}) else '',
        'Box Office Worldwide': page.find('li', {'data-testid': 'title-boxoffice-cumulativeworldwidegross'}).find('div').text if page.find('li', {'data-testid': 'title-boxoffice-cumulativeworldwidegross'}) else '',
        'Length': page.find('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers sc-afe43def-4 kdXikI baseAlt'}).find_all('li')[-1].text if page.find('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers sc-afe43def-4 kdXikI baseAlt'}) else '',
        'Rating': page.find('div', {'data-testid': 'hero-rating-bar__aggregate-rating__score'}).find('span').text if page.find('div', {'data-testid': 'hero-rating-bar__aggregate-rating__score'}) else '',
        'Director Names': ', '.join([director.text.strip() for director in page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})[0].find_all('li')]) if len(page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})) > 1 else '',
        'Director Links': ['https://www.imdb.com' + director.find('a').get('href').split('?')[0] for director in page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})[0].find_all('li')] if len(page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})) > 1 else '',
        'Cast Names': ', '.join([cast.text.strip() for cast in page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})[-1].find_all('li')]) if len(page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})) > 0 else '',
        'Cast Links': ['https://www.imdb.com' + director.find('a').get('href').split('?')[0] for director in page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})[-1].find_all('li')] if len(page.find_all('ul', {'class': 'ipc-inline-list ipc-inline-list--show-dividers ipc-inline-list--inline ipc-metadata-list-item__list-content baseAlt'})) > 0 else '',
    }

In [5]:
def get_title_awards(imdb_id):
    imdb_url = f'https://www.imdb.com/title/{imdb_id}/awards/'
    page = bs(requests.get(imdb_url, headers=headers).text, 'lxml')
    
    return ', '.join([award.find_all('td')[-1].text.strip() for award in page.find('table', {'class': 'awards'}).find_all('tr')]) if page.find('table', {'class': 'awards'}) else ''

In [6]:
df = pd.read_csv('original_movies.csv')

new_columns_to_add = [
    'Movie Budget',
    'Movie Box Office US/CA',
    'Movie Box Office Worldwide',
    'Movie Length',
    'Movie Rating',
    'Movie Director Names',
    'Movie Director Links',
    'Movie Cast Names',
    'Movie Cast Links',
    'Movie Awards',
   
]

for column in new_columns_to_add:
    if not column in df.columns:
        df.insert(loc=len(df.columns), column=column, value=['']*len(df), allow_duplicates=True)

In [7]:
for x in range(len(df)):
    imdb_id = df.iloc[x]['imdb_id']
    original_details = get_title_details(imdb_id)

    ##rIMDb_id = df.iloc[x]['rIMDb']
    ##remade_details = get_title_details(rIMDb_id)

    for key, value in original_details.items():
        df.at[x, f'Movie {key}'] = value

    #for key, value in remade_details.items():
        #df.at[x, f'Remade {key}'] = value

    df.at[x, 'Movie Awards'] = get_title_awards(imdb_id)
    #df.at[x, 'Remade Awards'] = get_title_awards(rIMDb_id)


    print(df.loc[x])
    df = df.fillna('')

    df.to_csv('StandAloneIMDb.csv', index=None)

imdb_id                                                               tt0066921
Movie Budget                                             $2,200,000 (estimated)
Movie Box Office US/CA                                              $26,617,553
Movie Box Office Worldwide                                          $26,960,374
Movie Length                                                             2h 16m
Movie Rating                                                                8.3
Movie Director Names                                            Stanley Kubrick
Movie Director Links                     [https://www.imdb.com/name/nm0000040/]
Movie Cast Names                 Malcolm McDowell, Patrick Magee, Michael Bates
Movie Cast Links              [https://www.imdb.com/name/nm0000532/, https:/...
Movie Awards                                                                   
Name: 0, dtype: object
imdb_id                                                               tt0347048
Movie Budget     

imdb_id                                                               tt0259711
Movie Budget                                            $68,000,000 (estimated)
Movie Box Office US/CA                                             $100,618,344
Movie Box Office Worldwide                                         $203,388,341
Movie Length                                                             2h 16m
Movie Rating                                                                6.9
Movie Director Names                                              Cameron Crowe
Movie Director Links                     [https://www.imdb.com/name/nm0001081/]
Movie Cast Names                        Tom Cruise, Penélope Cruz, Cameron Diaz
Movie Cast Links              [https://www.imdb.com/name/nm0000129/, https:/...
Movie Awards                                                                   
Name: 10, dtype: object
imdb_id                                                               tt1077258
Movie Budget    

imdb_id                                                               tt0099612
Movie Budget                                            $11,500,000 (estimated)
Movie Box Office US/CA                                                 $334,748
Movie Box Office Worldwide                                             $334,748
Movie Length                                                             1h 25m
Movie Rating                                                                5.4
Movie Director Names                                               Roger Corman
Movie Director Links                     [https://www.imdb.com/name/nm0000339/]
Movie Cast Names                            John Hurt, Raul Julia, Nick Brimble
Movie Cast Links              [https://www.imdb.com/name/nm0000457/, https:/...
Movie Awards                  Best Science Fiction Film, Best Director\nRoge...
Name: 20, dtype: object
imdb_id                                                               tt0219965
Movie Budget    

imdb_id                                                               tt0160399
Movie Budget                                            $30,000,000 (estimated)
Movie Box Office US/CA                                               $6,285,176
Movie Box Office Worldwide                                           $8,694,320
Movie Length                                                             1h 35m
Movie Rating                                                                6.2
Movie Director Names                                                Gary Fleder
Movie Director Links                     [https://www.imdb.com/name/nm0001219/]
Movie Cast Names                   Shane Brolly, Vincent D'Onofrio, Gary Sinise
Movie Cast Links              [https://www.imdb.com/name/nm0111274/, https:/...
Movie Awards                                                                   
Name: 30, dtype: object
imdb_id                                                               tt0072641
Movie Budget    

imdb_id                                                               tt0105328
Movie Budget                                         DEM 16,000,000 (estimated)
Movie Box Office US/CA                                                         
Movie Box Office Worldwide                                                     
Movie Length                                                             1h 55m
Movie Rating                                                                7.2
Movie Director Names                                               Helmut Dietl
Movie Director Links                     [https://www.imdb.com/name/nm0226200/]
Movie Cast Names              Götz George, Uwe Ochsenknecht, Christiane Hörb...
Movie Cast Links              [https://www.imdb.com/name/nm0313443/, https:/...
Movie Awards                                                                   
Name: 40, dtype: object
imdb_id                                                               tt0080573
Movie Budget    

...

imdb_id                                                               tt0177038
Movie Budget                                                                   
Movie Box Office US/CA                                                         
Movie Box Office Worldwide                                                     
Movie Length                                                             1h 30m
Movie Rating                                                                6.8
Movie Director Names                                            Eduard Zahariev
Movie Director Links                     [https://www.imdb.com/name/nm0755075/]
Movie Cast Names              Georgi Georgiev-Getz, Mikhail Mikhaylov, Georg...
Movie Cast Links              [https://www.imdb.com/name/nm0313768/, https:/...
Movie Awards                                                                   
Name: 6216, dtype: object
imdb_id                                                    tt0349884
Movie Budget             

imdb_id                                                    tt9359394
Movie Budget                                                        
Movie Box Office US/CA                                              
Movie Box Office Worldwide                                          
Movie Length                                                     58m
Movie Rating                                                     8.1
Movie Director Names                           Nina Maria Pashalidou
Movie Director Links          [https://www.imdb.com/name/nm3312401/]
Movie Cast Names                                          Aamir Khan
Movie Cast Links              [https://www.imdb.com/name/nm0451148/]
Movie Awards                                                        
Name: 6226, dtype: object
imdb_id                                                              tt13825564
Movie Budget                                                                   
Movie Box Office US/CA                                 

imdb_id                                                    tt21268098
Movie Budget                                                         
Movie Box Office US/CA                                               
Movie Box Office Worldwide                                           
Movie Length                                                     2022
Movie Rating                                                         
Movie Director Names                                  Arnaud Beaudoux
Movie Director Links          [https://www.imdb.com/name/nm13420926/]
Movie Cast Names                                      Arnaud Beaudoux
Movie Cast Links              [https://www.imdb.com/name/nm13420926/]
Movie Awards                                                         
Name: 6236, dtype: object
imdb_id                                                               tt4966210
Movie Budget                                                                   
Movie Box Office US/CA                      

imdb_id                                                              tt22984438
Movie Budget                                                                   
Movie Box Office US/CA                                                         
Movie Box Office Worldwide                                                     
Movie Length                                                                 3m
Movie Rating                                                                   
Movie Director Names                                           Kamal McAllister
Movie Director Links                    [https://www.imdb.com/name/nm14169974/]
Movie Cast Names               Amber Carstensen, Nyah Carlson, Kamal McAllister
Movie Cast Links              [https://www.imdb.com/name/nm13069007/, https:...
Movie Awards                                                                   
Name: 6246, dtype: object
imdb_id                                                              tt22311458
Movie Budget  

imdb_id                                                               tt1015187
Movie Budget                                                                   
Movie Box Office US/CA                                                         
Movie Box Office Worldwide                                                     
Movie Length                                                               2006
Movie Rating                                                                7.8
Movie Director Names                                                Paul Lamont
Movie Director Links                     [https://www.imdb.com/name/nm2616798/]
Movie Cast Names                             Armand Assante, David Ogden Stiers
Movie Cast Links              [https://www.imdb.com/name/nm0000800/, https:/...
Movie Awards                  Telecast - Professional Non-Fiction Division: ...
Name: 6256, dtype: object
imdb_id                                                               tt5135104
Movie Budget  